# 点航分支

In [ ]:
from sklearn.metrics import accuracy_score
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from sklearn.gaussian_process.kernels import RBF
from sktime.dists_kernels import AggrDist
from sktime.classification.distance_based import KNeighborsTimeSeriesClassifier
from sktime.classification.kernel_based import RocketClassifier, TimeSeriesSVC
from sktime.classification.hybrid import HIVECOTEV2
from sktime.classification.ensemble import WeightedEnsembleClassifier
from sktime.dists_kernels import FlatDist, ScipyDist
import plotly.graph_objects as go
import polars as pl
import numpy as np
import pickle
import os
import glob
import re

from data.track_preprocess import TrajectoryDataProcessor, process_df

In [ ]:
DATA_ROOT = r'D:\DataSets\挑战杯_揭榜挂帅_CQ-08赛题_数据集'
NUM_CLASSES = 4
SEQ_LEN = 29
ABNORMAL_BATCH_ID = [1451, 1452, 1457, 1462, 1467, 1469, 1473, 1478, 1484, 1487, 1488, 1490, 1494, 1496, 1497, 1500]

In [ ]:
# 查找支持多元时序分类的模型
from sktime.registry import all_estimators

all_estimators("classifier", filter_tags={"capability:multivariate": True}, as_dataframe=True)

In [ ]:
def get_data(data_root: str, num_classes: int, time: int):
    if time > SEQ_LEN:
        raise ValueError(f"time {time} should be less than or equal to SEQ_LEN {SEQ_LEN}")
    data = []
    labels = []

    point_files = glob.glob(os.path.join(data_root, '点迹/PointTracks_*.txt'))
    for point_file in point_files:
        match_result = re.match(r'PointTracks_(\d+)_(\d+)_(\d+).txt', os.path.basename(point_file))
        batch_id = int(match_result.group(1))
        label = int(match_result.group(2))
        num_tracks = int(match_result.group(3))
        if label > num_classes or batch_id in ABNORMAL_BATCH_ID:
            continue
        track_file = os.path.join(data_root, f"航迹/Tracks_{batch_id}_{label}_{num_tracks}.txt")

        preprocessed_data = TrajectoryDataProcessor(point_file, track_file).get_processed_data()
        point_df = pl.from_pandas(preprocessed_data['point_data'])
        track_df = pl.from_pandas(preprocessed_data['track_data'])
        df = point_df.join(track_df, on=["时间", "批号"], how="left").sort("时间")
        df = process_df(df)
        data_batch = df.to_numpy(order='c').astype(np.float64)
        if num_tracks >= time:
            data_batch = data_batch[:time, :]
        else:
            data_batch = np.concat([
                data_batch,
                np.stack([
                    data_batch[-1, :] for _ in range(time - num_tracks)
                ], axis=0)
            ], axis=0)
        data.append(data_batch)
        labels.append(label - 1)
    data = np.stack(data, axis=0)
    labels = np.array(labels)
    train_data, test_data, train_labels, test_labels = train_test_split(data, labels, test_size=0.2, random_state=42)
    # normalize
    train_scaler = StandardScaler()
    train_data = train_scaler.fit_transform(train_data.reshape(-1, train_data.shape[-1])).reshape(-1, time, train_data.shape[-1])
    test_scaler = StandardScaler()
    test_data = test_scaler.fit_transform(test_data.reshape(-1, test_data.shape[-1])).reshape(-1, time, test_data.shape[-1])
    return train_data, test_data, train_labels, test_labels, train_scaler, test_scaler

In [ ]:
def calc_acc(pred_labels, test_labels, num_classes):
    acc = accuracy_score(test_labels, pred_labels)
    acc_by_class = []
    for i in range(num_classes):
        acc_by_class.append(accuracy_score(test_labels[test_labels == i], pred_labels[test_labels == i]))
    return acc, acc_by_class

## KNN-TSC

In [ ]:
def train_and_test_KNN_TSC(k, save_path=None):
    euclidean_dist = FlatDist(ScipyDist())
    acc_by_time = []

    for t in range(1, SEQ_LEN + 1):
        train_data, test_data, train_labels, test_labels, train_scaler, test_scaler = get_data(DATA_ROOT, NUM_CLASSES, t)
        knn_tsc = KNeighborsTimeSeriesClassifier(n_neighbors=k, distance=euclidean_dist)
        knn_tsc.fit(train_data, train_labels)
        if save_path is not None:
            os.makedirs(save_path, exist_ok=True)
            filename = os.path.join(save_path, f"knn_tsc_{t}.pkl")
            with open(filename, "wb") as f:
                pickle.dump(knn_tsc, f)
        pred_labels = knn_tsc.predict(test_data)
        acc, acc_by_class = calc_acc(pred_labels, test_labels, NUM_CLASSES)
        print(f"------------- Time {t} -------------")
        print(f"Accuracy: {acc}")
        acc_by_time.append(acc)
        for i in range(NUM_CLASSES):
            print(f"Accuracy of class {i+1}: {acc_by_class[i]}")
    return acc_by_time

In [ ]:
fig = go.Figure()
for k in [1, 3, 5, 7, 9]:
    acc_by_time = train_and_test_KNN_TSC(k)
    fig.add_trace(go.Scatter(x=list(range(1, SEQ_LEN+1)), y=acc_by_time, name=f"K={k}", mode="lines"))
fig.update_layout(title="KNN-TSC Accuracy by Time", xaxis_title="Time", yaxis_title="Accuracy")
fig.show()
# select k=3

In [ ]:
fig = go.Figure()
acc_by_time = train_and_test_KNN_TSC(k=3, save_path="./track_models/knn_tsc")
fig.add_trace(go.Scatter(x=list(range(1, SEQ_LEN+1)), y=acc_by_time, mode="lines"))
fig.update_layout(title="KNN-TSC Accuracy by Time", xaxis_title="Time", yaxis_title="Accuracy")
fig.show()

## ROCKET

In [32]:
def train_and_test_ROCKET_TSC(num_kernels, save_path=None):
    acc_by_time = []
    for t in range(1, SEQ_LEN + 1):
        train_data, test_data, train_labels, test_labels, train_scaler, test_scaler = get_data(DATA_ROOT, NUM_CLASSES, t)
        rocket_tsc = RocketClassifier(rocket_transform="multirocket", num_kernels=num_kernels, random_state=42)
        rocket_tsc.fit(train_data, train_labels)
        if save_path is not None:
            os.makedirs(save_path, exist_ok=True)
            filename = os.path.join(save_path, f"rocket_tsc_{t}.pkl")
            with open(filename, "wb") as f:
                pickle.dump(rocket_tsc, f)
        pred_labels = rocket_tsc.predict(test_data)
        acc, acc_by_class = calc_acc(pred_labels, test_labels, NUM_CLASSES)
        print(f"------------- Time {t} -------------")
        print(f"Accuracy: {acc}")
        acc_by_time.append(acc)
        for i in range(NUM_CLASSES):
            print(f"Accuracy of class {i+1}: {acc_by_class[i]}")
    return acc_by_time

In [ ]:
fig = go.Figure()
for num_kernels in [1000, 2000, 5000, 10000, 20000]:
    acc_by_time = train_and_test_ROCKET_TSC(num_kernels)
    fig.add_trace(go.Scatter(x=list(range(1, SEQ_LEN+1)), y=acc_by_time, name=f"K={num_kernels}", mode="lines"))
fig.update_layout(title="ROCKET Accuracy by Time", xaxis_title="Time", yaxis_title="Accuracy")
fig.show()
# select num_kernels=10000

In [33]:
fig = go.Figure()
acc_by_time = train_and_test_ROCKET_TSC(num_kernels=10000, save_path="./track_models/rocket_tsc")
fig.add_trace(go.Scatter(x=list(range(1, SEQ_LEN+1)), y=acc_by_time, mode="lines"))
fig.update_layout(title="ROCKET Accuracy by Time", xaxis_title="Time", yaxis_title="Accuracy")
fig.show()

C:\Users\27344\codespace\codes\ObjectTracking\ensemble\data\track_preprocess.py:288: FutureWarning:

Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '7399314.333333331' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.

C:\Users\27344\codespace\codes\ObjectTracking\ensemble\data\track_preprocess.py:399: FutureWarning:

Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '[5720083.         7640677.         6499358.         7399314.33333333
 8561698.         2925092.          582255.         2391100.
  858322.         1008002.         4644832.         1809684.
 2517474.         3830768.          398214.        ]' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.

C:\Users\27344\codespace\codes\ObjectTracking\ensemble\data\track_preprocess.py:288: FutureWarning:

Setting an item of incompatib

------------- Time 1 -------------
Accuracy: 0.8628158844765343
Accuracy of class 1: 0.7971014492753623
Accuracy of class 2: 0.967741935483871
Accuracy of class 3: 0.75
Accuracy of class 4: 0.9459459459459459


C:\Users\27344\codespace\codes\ObjectTracking\ensemble\data\track_preprocess.py:288: FutureWarning:

Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '7399314.333333331' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.

C:\Users\27344\codespace\codes\ObjectTracking\ensemble\data\track_preprocess.py:399: FutureWarning:

Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '[5720083.         7640677.         6499358.         7399314.33333333
 8561698.         2925092.          582255.         2391100.
  858322.         1008002.         4644832.         1809684.
 2517474.         3830768.          398214.        ]' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.

C:\Users\27344\codespace\codes\ObjectTracking\ensemble\data\track_preprocess.py:288: FutureWarning:

Setting an item of incompatib

------------- Time 2 -------------
Accuracy: 0.8916967509025271
Accuracy of class 1: 0.8260869565217391
Accuracy of class 2: 0.9354838709677419
Accuracy of class 3: 0.8333333333333334
Accuracy of class 4: 0.972972972972973


C:\Users\27344\codespace\codes\ObjectTracking\ensemble\data\track_preprocess.py:288: FutureWarning:

Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '7399314.333333331' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.

C:\Users\27344\codespace\codes\ObjectTracking\ensemble\data\track_preprocess.py:399: FutureWarning:

Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '[5720083.         7640677.         6499358.         7399314.33333333
 8561698.         2925092.          582255.         2391100.
  858322.         1008002.         4644832.         1809684.
 2517474.         3830768.          398214.        ]' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.

C:\Users\27344\codespace\codes\ObjectTracking\ensemble\data\track_preprocess.py:288: FutureWarning:

Setting an item of incompatib

...

------------- Time 27 -------------
Accuracy: 0.9494584837545126
Accuracy of class 1: 0.927536231884058
Accuracy of class 2: 0.9838709677419355
Accuracy of class 3: 0.9166666666666666
Accuracy of class 4: 0.972972972972973


C:\Users\27344\codespace\codes\ObjectTracking\ensemble\data\track_preprocess.py:288: FutureWarning:

Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '7399314.333333331' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.

C:\Users\27344\codespace\codes\ObjectTracking\ensemble\data\track_preprocess.py:399: FutureWarning:

Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '[5720083.         7640677.         6499358.         7399314.33333333
 8561698.         2925092.          582255.         2391100.
  858322.         1008002.         4644832.         1809684.
 2517474.         3830768.          398214.        ]' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.

C:\Users\27344\codespace\codes\ObjectTracking\ensemble\data\track_preprocess.py:288: FutureWarning:

Setting an item of incompatib

------------- Time 28 -------------
Accuracy: 0.9386281588447654
Accuracy of class 1: 0.8985507246376812
Accuracy of class 2: 0.9838709677419355
Accuracy of class 3: 0.9027777777777778
Accuracy of class 4: 0.972972972972973


C:\Users\27344\codespace\codes\ObjectTracking\ensemble\data\track_preprocess.py:288: FutureWarning:

Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '7399314.333333331' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.

C:\Users\27344\codespace\codes\ObjectTracking\ensemble\data\track_preprocess.py:399: FutureWarning:

Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '[5720083.         7640677.         6499358.         7399314.33333333
 8561698.         2925092.          582255.         2391100.
  858322.         1008002.         4644832.         1809684.
 2517474.         3830768.          398214.        ]' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.

C:\Users\27344\codespace\codes\ObjectTracking\ensemble\data\track_preprocess.py:288: FutureWarning:

Setting an item of incompatib

------------- Time 29 -------------
Accuracy: 0.9458483754512635
Accuracy of class 1: 0.9130434782608695
Accuracy of class 2: 0.967741935483871
Accuracy of class 3: 0.9305555555555556
Accuracy of class 4: 0.972972972972973


## SVC

In [ ]:
def train_and_test_SVC():
    acc_by_time = []
    for t in range(1, SEQ_LEN + 1):
        train_data, test_data, train_labels, test_labels, train_scaler, test_scaler = get_data(DATA_ROOT, NUM_CLASSES, t)
        svc_tsc = TimeSeriesSVC(kernel=AggrDist(RBF()), random_state=42)
        svc_tsc.fit(train_data, train_labels)
        pred_labels = svc_tsc.predict(test_data)
        acc, acc_by_class = calc_acc(pred_labels, test_labels, NUM_CLASSES)
        print(f"------------- Time {t} -------------")
        print(f"Accuracy: {acc}")
        acc_by_time.append(acc)
        for i in range(NUM_CLASSES):
            print(f"Accuracy of class {i+1}: {acc_by_class[i]}")
    return acc_by_time

In [ ]:
fig = go.Figure()
acc_by_time = train_and_test_SVC()
fig.add_trace(go.Scatter(x=list(range(1, SEQ_LEN+1)), y=acc_by_time, name="SVC", mode="lines"))
fig.update_layout(title="SVC Accuracy by Time", xaxis_title="Time", yaxis_title="Accuracy")
fig.show()
# exclude SVC

## HIVECOTEV2

In [ ]:
def train_and_test_HIVECOTEV2():
    acc_by_time = []
    for t in range(1, SEQ_LEN + 1):
        train_data, test_data, train_labels, test_labels, train_scaler, test_scaler = get_data(DATA_ROOT, NUM_CLASSES, t)
        hivecotev2_tsc = HIVECOTEV2(random_state=42)
        hivecotev2_tsc.fit(train_data, train_labels)
        pred_labels = hivecotev2_tsc.predict(test_data)
        acc, acc_by_class = calc_acc(pred_labels, test_labels, NUM_CLASSES)
        print(f"------------- Time {t} -------------")
        print(f"Accuracy: {acc}")
        acc_by_time.append(acc)
        for i in range(NUM_CLASSES):
            print(f"Accuracy of class {i+1}: {acc_by_class[i]}")
    return acc_by_time

In [ ]:
fig = go.Figure()
acc_by_time = train_and_test_HIVECOTEV2()
fig.add_trace(go.Scatter(x=list(range(1, SEQ_LEN+1)), y=acc_by_time, name="HIVECOTEV2", mode="lines"))
fig.update_layout(title="HIVECOTEV2 Accuracy by Time", xaxis_title="Time", yaxis_title="Accuracy")
fig.show()

a## WE

In [ ]:
def train_and_test_WE():
    acc_by_time = []
    for t in range(1, SEQ_LEN + 1):
        train_data, test_data, train_labels, test_labels, train_scaler, test_scaler = get_data(DATA_ROOT, NUM_CLASSES, t)
        we_tsc = WeightedEnsembleClassifier(
            [
                ("KNN-TSC", KNeighborsTimeSeriesClassifier(n_neighbors=3, distance=FlatDist(ScipyDist()))),
                ("ROCKET", RocketClassifier(num_kernels=20000, random_state=42)),
            ],
            weights=[2, 1, 1, 1],
        )
        we_tsc.fit(train_data, train_labels)
        pred_labels = we_tsc.predict(test_data)
        acc, acc_by_class = calc_acc(pred_labels, test_labels, NUM_CLASSES)
        print(f"------------- Time {t} -------------")
        print(f"Accuracy: {acc}")
        acc_by_time.append(acc)
        for i in range(NUM_CLASSES):
            print(f"Accuracy of class {i+1}: {acc_by_class[i]}")
    return acc_by_time

In [ ]:
fig = go.Figure()
acc_by_time = train_and_test_WE()
fig.add_trace(go.Scatter(x=list(range(1, SEQ_LEN+1)), y=acc_by_time, name="WE", mode="lines"))
fig.update_layout(title="WE Accuracy by Time", xaxis_title="Time", yaxis_title="Accuracy")
fig.show()